This Notebook is a Stable-diffusion tool which allows you to find similiar tokens from the SD 1.5 vocab.json that you can use for text-to-image generation. Try this Free online SD 1.5 generator with the results: https://perchance.org/fusion-ai-image-generator

Scroll to the bottom of the notebook to see the guide for how this works.

In [ ]:
# @title ✳️ Load/initialize values
# Load the tokens into the colab
!git clone https://huggingface.co/datasets/codeShare/sd_tokens
import torch
from torch import linalg as LA
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
%cd /content/sd_tokens
token = torch.load('sd15_tensors.pt', map_location=device, weights_only=True)
#-----#

#Import the vocab.json
import json
import pandas as pd
with open('vocab.json', 'r') as f:
    data = json.load(f)

_df = pd.DataFrame({'count': data})['count']

vocab = {
    value: key for key, value in _df.items()
}
#-----#

# Define functions/constants
NUM_TOKENS = 49407

def absolute_value(x):
    return max(x, -x)


def token_similarity(A, B):

  #Vector length#
  _A = LA.vector_norm(A, ord=2)
  _B = LA.vector_norm(B, ord=2)

  #----#
  result = torch.dot(A,B)/(_A*_B)
  #similarity_pcnt = absolute_value(result.item()*100)
  similarity_pcnt = result.item()*100
  similarity_pcnt_aprox = round(similarity_pcnt, 3)
  result = f'{similarity_pcnt_aprox} %'
  return result


def similarity(id_A , id_B):
  #Tensors
  A = token[id_A]
  B = token[id_B]
  return token_similarity(A, B)
#----#

#print(vocab[8922]) #the vocab item for ID 8922
#print(token[8922].shape)  #dimension of the token

mix_with = ""
mix_method = "None"

#-------------#
# UNUSED

# Get the 10 lowest values from a tensor as a string
def get_valleys (A):
  sorted, indices = torch.sort(A,dim=0 , descending=False)
  result = "{"
  for index in range(10):
    id = indices[index].item()
    result = result + f"{id}"
    if(index<9):
      result = result + ","
  result = result + "}"
  return result

# Get the 10 highest values from a tensor as a string
def get_peaks (A):
  sorted, indices = torch.sort(A,dim=0 , descending=True)
  result = "{"
  for index in range(10):
    id = indices[index].item()
    result = result + f"{id}"
    if(index<9):
      result = result + ","
  result = result + "}"
  return result

In [ ]:
# @title ⚡ Get similiar tokens
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14", clean_up_tokenization_spaces = False)

# @markdown Write name of token to match against
prompt= "banana" # @param {type:'string',"placeholder":"leave empty for random value token"}

tokenizer_output = tokenizer(text = prompt)
input_ids = tokenizer_output['input_ids']
print(input_ids)


#The prompt will be enclosed with the <|start-of-text|> and <|end-of-text|> tokens, which is why output will be [49406, ... , 49407].

#You can leave the 'prompt' field empty to get a random value tensor. Since the tensor is random value, it will not correspond to any tensor in the vocab.json list , and this it will have no ID.

id_A = input_ids[1]
A = token[id_A]
_A = LA.vector_norm(A, ord=2)

#if no imput exists we just randomize the entire thing
if (prompt == ""):
  id_A = -1
  print("Tokenized prompt tensor A is a random valued tensor with no ID")
  R = torch.rand(768)
  _R =  LA.vector_norm(R, ord=2)
  A = R*(_A/_R)
  name_A = 'random_A'

# @markdown (optional) Mix the token with something else
mix_with = "" # @param {"type":"string","placeholder":"leave empty for random value token"}
mix_method = "None" # @param ["None" , "Average", "Subtract"] {allow-input: true}
w = 0.5 # @param {type:"slider", min:0, max:1, step:0.01}

# @markdown Limit char size of included token
min_char_size = 3 # @param {type:"slider", min:0, max: 50, step:1}
char_range = 5 # @param {type:"slider", min:0, max: 50, step:1}

tokenizer_output = tokenizer(text = mix_with)
input_ids = tokenizer_output['input_ids']
id_C = input_ids[1]
C = token[id_C]
_C = LA.vector_norm(C, ord=2)

#if no imput exists we just randomize the entire thing
if (mix_with == ""):
  id_C = -1
  print("Tokenized prompt  'mix_with' tensor C is a random valued tensor with no ID")
  R = torch.rand(768)
  _R =  LA.vector_norm(R, ord=2)
  C = R*(_C/_R)
  name_C = 'random_C'

name_A = "A of random type"
if (id_A>-1):
  name_A = vocab[id_A]

name_C = "token C of random type"
if (id_C>-1):
  name_C = vocab[id_C]

# Peaks feature
#peaks_A = get_valleys(A)
#peaks_C = get_valleys(C)
#print(f"The elementwise top 10 highest values for A is at indices {peaks_A}")
#print("-------")
#print(f"The elementwise top 10 highest values for C is at indices {peaks_C}")
#print("-------")
#//------//

print(f"The similarity between A '{name_A}' and C '{name_C}' is {token_similarity(A, C)}")

if (mix_method ==  "None"):
  print("No operation")

if (mix_method ==  "Average"):
  A = w*A + (1-w)*C
  _A = LA.vector_norm(A, ord=2)
  print(f"Tokenized prompt tensor A '{name_A}' token has been recalculated as A = w*A + (1-w)*C , where C is '{name_C}' token , for w = {w}  ")

if (mix_method ==  "Subtract"):
  tmp =  w*A - (1-w)*C
  _tmp =  LA.vector_norm(tmp, ord=2)
  A = (_A/_tmp)*tmp
  #//---//
  _A = LA.vector_norm(A, ord=2)
  print(f"Tokenized prompt tensor A '{name_A}' token has been recalculated as A = _A*norm(w*A  - (1-w)*C) , where C is '{name_C}' token , for w = {w} ")

#OPTIONAL : Add/subtract + normalize above result with another token. Leave field empty to get a random value tensor

dots = torch.zeros(NUM_TOKENS)
for index in range(NUM_TOKENS):
  id_B = index
  B = token[id_B]
  _B = LA.vector_norm(B, ord=2)
  result = torch.dot(A,B)/(_A*_B)
  #result = absolute_value(result.item())
  result = result.item()
  dots[index] = result


sorted, indices = torch.sort(dots,dim=0 , descending=True)
#----#
if (mix_method ==  "Average"):
  print(f'Calculated all cosine-similarities between the average of token {name_A} and {name_C} with Id_A = {id_A} and mixed Id_C = {id_C} as a 1x{sorted.shape[0]} tensor')
if (mix_method ==  "Subtract"):
  print(f'Calculated all cosine-similarities between the subtract of token {name_A} and {name_C} with Id_A = {id_A} and mixed Id_C = {id_C} as a 1x{sorted.shape[0]} tensor')
if (mix_method ==  "None"):
  print(f'Calculated all cosine-similarities between the token {name_A} with Id_A = {id_A} with the the rest of the {NUM_TOKENS} tokens as a 1x{sorted.shape[0]} tensor')

#Produce a list id IDs that are most similiar to the prompt ID at positiion 1 based on above result

# @markdown Set print options
list_size = 100 # @param {type:'number'}
print_ID = False # @param {type:"boolean"}
print_Similarity = True # @param {type:"boolean"}
print_Name = True # @param {type:"boolean"}
print_Divider = True # @param {type:"boolean"}


if (print_Divider):
  print('//---//')

print('')
print('Here is the result : ')
print('')

for index in range(list_size):
  id = indices[index].item()
  if (print_Name):
    print(f'{vocab[id]}') # vocab item
  if (print_ID):
    print(f'ID = {id}') # IDs
  if (print_Similarity):
    print(f'similiarity = {round(sorted[index].item()*100,2)} %')
  if (print_Divider):
    print('--------')

#Print the sorted list from above result

In [ ]:
# @title 💫 Compare Text encodings

prompt_A = "banana" # @param {"type":"string","placeholder":"Write a prompt"}
prompt_B = "" # @param {"type":"string","placeholder":"Write a prompt"}
use_token_padding = True # @param {type:"boolean"}

from transformers import  CLIPProcessor, CLIPModel

processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14" , clean_up_tokenization_spaces = True)

model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14")

ids_A = processor.tokenizer(text=prompt_A, padding=use_token_padding, return_tensors="pt")
text_encoding_A = model.get_text_features(**ids_A)


ids_B = processor.tokenizer(text=prompt_B, padding=use_token_padding, return_tensors="pt")
text_encoding_B = model.get_text_features(**ids_B)

similarity_str =  'The similarity between the text_encoding for A:"' + prompt_A + '" and B: "' + prompt_B +'" is ' +  token_similarity(text_encoding_A[0] , text_encoding_B[0])


print(similarity_str)
#outputs = model(**inputs)
#logits_per_image = outputs.logits_per_image # this is the image-text similarity score
#probs = logits_per_image.softmax(dim=1) # we can take the softmax to get the label probabilities

In [9]:
# @title 🪐🖼️ -> 📝 Image to prompt : Add single token to existing prompt to match image
from google.colab import files
def getLocalFiles():
    _files = files.upload()
    if len(_files) >0:
       for k,v in _files.items():
         open(k,'wb').write(v)

#Get image
# You can use "http://images.cocodataset.org/val2017/000000039769.jpg" for testing
url = "http://images.cocodataset.org/val2017/000000039769.jpg" # @param {"type":"string","placeholder":"leave empty for local upload"}
from PIL import Image
import requests
if url == "":
  image_A = getLocalFiles()
else:
  image_A = Image.open(requests.get(url, stream=True).raw)


# Get image features
from transformers import  CLIPProcessor, CLIPModel
processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14" , clean_up_tokenization_spaces = True)
model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14")
inputs = processor(images=image_A, return_tensors="pt")
image_features = model.get_image_features(**inputs)
text_encoding_A = image_features
A =  text_encoding_A[0]
_A = LA.vector_norm(A, ord=2)
prompt_A = "the image"
name_A = prompt_A
#-----#

# @markdown Set conditions for the output
must_start_with = "" # @param {"type":"string","placeholder":"write a text"}
must_contain = "" # @param {"type":"string","placeholder":"write a text"}
must_end_with = "" # @param {"type":"string","placeholder":"write a text"}
token_B = must_contain

# @markdown Limit the search
use_token_padding = True # @param {type:"boolean"}
start_search_at_ID = 12500 # @param {type:"slider", min:0, max: 49407, step:100}
search_range = 500 # @param {type:"slider", min:0, max: 2000, step:100}
restrictions = 'Suffix only' # @param ["None", "Suffix only", "Prefix only"]

# @markdown Limit char size of included token
min_char_size = 3 # @param {type:"slider", min:0, max: 50, step:1}
char_range = 5 # @param {type:"slider", min:0, max: 50, step:1}

#Tokenize input B
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14", clean_up_tokenization_spaces = False)
tokenizer_output = tokenizer(text = token_B)
input_ids = tokenizer_output['input_ids']
#-----#
name_B = must_contain
#-----#

START = start_search_at_ID
RANGE =  min(search_range , 49407 - start_search_at_ID)

dots = torch.zeros(RANGE)
is_BC = torch.zeros(RANGE)
for index in range(RANGE):
  id_C = START + index
  C = token[id_C]
  _C = LA.vector_norm(C, ord=2)
  name_C = vocab[id_C]

  # Decide if we should process prefix/suffix tokens
  if name_C.find('</w>')<=-1:
    if restrictions != "Prefix only":
      continue
  else:
    if restrictions == "Prefix only":
      continue
  #-----#

  # Decide if char-size is within range
  if len(name_C) < min_char_size:
    continue
  if len(name_C) > min_char_size + char_range:
    continue
  #-----#

  name_CB = must_start_with + name_C + name_B + must_end_with
  if restrictions == "Prefix only":
    name_CB = must_start_with +  name_C + '-' + name_B + must_end_with
  #-----#
  ids_CB = processor.tokenizer(text=name_CB, padding=use_token_padding, return_tensors="pt")
  text_encoding_CB = model.get_text_features(**ids_CB)
  CB = text_encoding_CB[0]
  _CB =  LA.vector_norm(CB, ord=2)
  sim_CB = torch.dot(A,CB)/(_A*_CB)
  #-----#
  if restrictions == "Prefix only":
    result = sim_CB
    result = result.item()
    dots[index] = result
    continue
  #-----#
  name_BC = must_start_with + name_B + name_C + must_end_with
  ids_BC = processor.tokenizer(text=name_BC, padding=use_token_padding, return_tensors="pt")
  text_encoding_BC = model.get_text_features(**ids_BC)
  BC = text_encoding_BC[0]
  _BC =  LA.vector_norm(BC, ord=2)
  sim_BC = torch.dot(A,BC)/(_A*_BC)
  #-----#

  result = sim_CB
  if(sim_BC > sim_CB):
    is_BC[index] = 1
    result = sim_BC

  #result = absolute_value(result.item())
  result = result.item()
  dots[index] = result
#----#

sorted, indices = torch.sort(dots,dim=0 , descending=True)

# @markdown Print options
list_size = 100 # @param {type:'number'}
print_ID = False # @param {type:"boolean"}
print_Similarity = True # @param {type:"boolean"}
print_Name = True # @param {type:"boolean"}
print_Divider = True # @param {type:"boolean"}


if (print_Divider):
  print('//---//')

print('')
print(f'These token pairings within the range ID = {START} to ID = {START + RANGE} most closely match the text_encoding for {prompt_A} : ')
print('')

for index in range(min(list_size,RANGE)):
  id = START + indices[index].item()
  if (print_Name):
    if(is_BC[index]>0):
      print(must_start_with +  name_B + vocab[id] + must_end_with)
    else:
      if restrictions == "Prefix only":
        print(must_start_with +   vocab[id] + '-'  + name_B + must_end_with)
      else:
        print(must_start_with +   vocab[id] + name_B + must_end_with)
  if (print_ID):
    print(f'ID = {id}') # IDs
  if (print_Similarity):
    print(f'similiarity = {round(sorted[index].item()*100,2)} %')
  if (print_Divider):
    print('--------')







//---//

These token pairings within the range ID = 12500 to ID = 13000 most closely match the text_encoding for the prompt "the image" : 

sits</w>yellow
similiarity = 23.02 %
--------
neys</w>yellow
similiarity = 19.74 %
--------
cody</w>yellow
similiarity = 18.61 %
--------
wns</w>yellow
similiarity = 18.43 %
--------
java</w>yellow
similiarity = 18.15 %
--------
jj</w>yellow
similiarity = 18.03 %
--------
eno</w>yellow
similiarity = 17.87 %
--------
cled</w>yellow
similiarity = 17.85 %
--------
nom</w>yellow
similiarity = 17.75 %
--------
dads</w>yellow
similiarity = 17.5 %
--------
mil</w>yellow
similiarity = 17.47 %
--------
whom</w>yellow
similiarity = 17.37 %
--------
itv</w>yellow
similiarity = 17.34 %
--------
vibe</w>yellow
similiarity = 17.2 %
--------
noir</w>yellow
similiarity = 17.14 %
--------
yellowarel</w>
similiarity = 17.1 %
--------
#âĢ¦</w>yellow
similiarity = 17.04 %
--------
maya</w>yellow
similiarity = 17.03 %
--------
yellowbam</w>
similiarity = 17.01 %
------

In [ ]:
# @title 🪐📝 Prompt to prompt : Add single token to existing prompt to match another prompt
# @markdown Write a text to match against...
prompt_A = "photo of a banana" # @param {"type":"string","placeholder":"Write a prompt"}

# @markdown Set conditions for the output
must_start_with = "" # @param {"type":"string","placeholder":"write a text"}
must_contain = "yellow" # @param {"type":"string","placeholder":"write a text"}
must_end_with = "" # @param {"type":"string","placeholder":"write a text"}
token_B = must_contain

# @markdown Limit the search
use_token_padding = True # @param {type:"boolean"}
start_search_at_ID = 12500 # @param {type:"slider", min:0, max: 49407, step:100}
search_range = 500 # @param {type:"slider", min:0, max: 2000, step:100}
restrictions = 'Suffix only' # @param ["None", "Suffix only", "Prefix only"]

# @markdown Limit char size of included token
min_char_size = 3 # @param {type:"slider", min:0, max: 50, step:1}
char_range = 5 # @param {type:"slider", min:0, max: 50, step:1}

#Tokenize input B
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14", clean_up_tokenization_spaces = False)
tokenizer_output = tokenizer(text = token_B)
input_ids = tokenizer_output['input_ids']
#-----#
name_B = must_contain
#-----#

from transformers import  CLIPProcessor, CLIPModel
processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14" , clean_up_tokenization_spaces = True)
model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14")
#-------#
ids_A = processor.tokenizer(text=prompt_A, padding=use_token_padding, return_tensors="pt")
text_encoding_A = model.get_text_features(**ids_A)
A =  text_encoding_A[0]
_A = LA.vector_norm(A, ord=2)
name_A = prompt_A
print(f'a text_encoding was created for the prompt "{prompt_A}" ')
print('')
#----#

START = start_search_at_ID
RANGE =  min(search_range , 49407 - start_search_at_ID)

dots = torch.zeros(RANGE)
is_BC = torch.zeros(RANGE)
for index in range(RANGE):
  id_C = START + index
  C = token[id_C]
  _C = LA.vector_norm(C, ord=2)
  name_C = vocab[id_C]

  # Decide if we should process prefix/suffix tokens
  if name_C.find('</w>')<=-1:
    if restrictions != "Prefix only":
      continue
  else:
    if restrictions == "Prefix only":
      continue
  #-----#

  # Decide if char-size is within range
  if len(name_C) < min_char_size:
    continue
  if len(name_C) > min_char_size + char_range:
    continue
  #-----#

  name_CB = must_start_with + name_C + name_B + must_end_with
  if restrictions == "Prefix only":
    name_CB = must_start_with +  name_C + '-' + name_B + must_end_with
  #-----#
  ids_CB = processor.tokenizer(text=name_CB, padding=use_token_padding, return_tensors="pt")
  text_encoding_CB = model.get_text_features(**ids_CB)
  CB = text_encoding_CB[0]
  _CB =  LA.vector_norm(CB, ord=2)
  sim_CB = torch.dot(A,CB)/(_A*_CB)
  #-----#
  if restrictions == "Prefix only":
    result = sim_CB
    result = result.item()
    dots[index] = result
    continue
  #-----#
  name_BC = must_start_with + name_B + name_C + must_end_with
  ids_BC = processor.tokenizer(text=name_BC, padding=use_token_padding, return_tensors="pt")
  text_encoding_BC = model.get_text_features(**ids_BC)
  BC = text_encoding_BC[0]
  _BC =  LA.vector_norm(BC, ord=2)
  sim_BC = torch.dot(A,BC)/(_A*_BC)
  #-----#

  result = sim_CB
  if(sim_BC > sim_CB):
    is_BC[index] = 1
    result = sim_BC

  #result = absolute_value(result.item())
  result = result.item()
  dots[index] = result
#----#

sorted, indices = torch.sort(dots,dim=0 , descending=True)

# @markdown Print options
list_size = 100 # @param {type:'number'}
print_ID = False # @param {type:"boolean"}
print_Similarity = True # @param {type:"boolean"}
print_Name = True # @param {type:"boolean"}
print_Divider = True # @param {type:"boolean"}


if (print_Divider):
  print('//---//')

print('')
print(f'These token pairings within the range ID = {START} to ID = {START + RANGE} most closely match the text_encoding for the prompt "{prompt_A}" : ')
print('')

for index in range(min(list_size,RANGE)):
  id = START + indices[index].item()
  if (print_Name):
    if(is_BC[index]>0):
      print(must_start_with +  name_B + vocab[id] + must_end_with)
    else:
      if restrictions == "Prefix only":
        print(must_start_with +   vocab[id] + '-'  + name_B + must_end_with)
      else:
        print(must_start_with +   vocab[id] + name_B + must_end_with)
  if (print_ID):
    print(f'ID = {id}') # IDs
  if (print_Similarity):
    print(f'similiarity = {round(sorted[index].item()*100,2)} %')
  if (print_Divider):
    print('--------')

#  ↓ Sub modules (use these to build your own projects) ↓

In [ ]:
# @title 📝 -> 🆔 Tokenize prompt into IDs
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14", clean_up_tokenization_spaces = False)

prompt= "banana" # @param {type:'string'}

tokenizer_output = tokenizer(text = prompt)
input_ids = tokenizer_output['input_ids']
print(input_ids)


#The prompt will be enclosed with the <|start-of-text|> and <|end-of-text|> tokens, which is why output will be [49406, ... , 49407].

#You can leave the 'prompt' field empty to get a random value tensor. Since the tensor is random value, it will not correspond to any tensor in the vocab.json list , and this it will have no ID.

In [ ]:
# @title 🆔->🥢 Take the ID at index 1 from above result and get its corresponding tensor value

id_A = input_ids[1]
A = token[id_A]
_A = LA.vector_norm(A, ord=2)

#if no imput exists we just randomize the entire thing
if (prompt == ""):
  id_A = -1
  print("Tokenized prompt tensor A is a random valued tensor with no ID")
  R = torch.rand(768)
  _R =  LA.vector_norm(R, ord=2)
  A = R*(_A/_R)

#Save a copy of the tensor A
id_P = id_A
P = A
_P = LA.vector_norm(A, ord=2)


In [ ]:
# @title 🥢 -> 🥢🔀 Take the ID at index 1 from above result and modify it (optional)
mix_with = "" # @param {type:'string'}
mix_method = "None" # @param ["None" , "Average", "Subtract"] {allow-input: true}
w = 0.5 # @param {type:"slider", min:0, max:1, step:0.01}

#------#
#If set to TRUE , this will use the output of this cell , tensor A, as the input of this cell the 2nd time we run it. Use this feature to mix many tokens into A
re_iterate_tensor_A = True # @param {"type":"boolean"}
if (re_iterate_tensor_A == False) :
  #prevent re-iterating A by reading from stored copy
  id_A = id_P
  A = P
  _A = _P
#----#

tokenizer_output = tokenizer(text = mix_with)
input_ids = tokenizer_output['input_ids']
id_C = input_ids[1]
C = token[id_C]
_C = LA.vector_norm(C, ord=2)

#if no imput exists we just randomize the entire thing
if (mix_with == ""):
  id_C = -1
  print("Tokenized prompt  'mix_with' tensor C is a random valued tensor with no ID")
  R = torch.rand(768)
  _R =  LA.vector_norm(R, ord=2)
  C = R*(_C/_R)

if (mix_method ==  "None"):
  print("No operation")

if (mix_method ==  "Average"):
  A = w*A + (1-w)*C
  _A = LA.vector_norm(A, ord=2)
  print("Tokenized prompt tensor A has been recalculated as A = w*A + (1-w)*C , where C is the tokenized prompt  'mix_with' tensor C")

if (mix_method ==  "Subtract"):
  tmp = (A/_A) - (C/_C)
  _tmp = LA.vector_norm(tmp, ord=2)
  A = tmp*((w*_A + (1-w)*_C)/_tmp)
  _A = LA.vector_norm(A, ord=2)
  print("Tokenized prompt tensor A has been recalculated as A = (w*_A + (1-w)*_C) * norm(w*A - (1-w)*C) , where C is the tokenized prompt 'mix_with' tensor C")

#OPTIONAL : Add/subtract + normalize above result with another token. Leave field empty to get a random value tensor

In [ ]:

# @title 🥢->🧾🥢 Find Similiar Tokens to ID at index 1 from above result
dots = torch.zeros(NUM_TOKENS)
for index in range(NUM_TOKENS):
  id_B = index
  B = token[id_B]
  _B = LA.vector_norm(B, ord=2)
  result = torch.dot(A,B)/(_A*_B)
  #result = absolute_value(result.item())
  result = result.item()
  dots[index] = result

name_A = "A of random type"
if (id_A>-1):
  name_A = vocab[id_A]

name_C = "token C of random type"
if (id_C>-1):
  name_C = vocab[id_C]


sorted, indices = torch.sort(dots,dim=0 , descending=True)
#----#
if (mix_method ==  "Average"):
  print(f'Calculated all cosine-similarities between the average of token {name_A} and {name_C} with Id_A = {id_A} and mixed Id_C = {id_C} as a 1x{sorted.shape[0]} tensor')
if (mix_method ==  "Subtract"):
  print(f'Calculated all cosine-similarities between the subtract of token {name_A} and {name_C} with Id_A = {id_A} and mixed Id_C = {id_C} as a 1x{sorted.shape[0]} tensor')
if (mix_method ==  "None"):
  print(f'Calculated all cosine-similarities between the token {name_A} with Id_A = {id_A} with the the rest of the {NUM_TOKENS} tokens as a 1x{sorted.shape[0]} tensor')

#Produce a list id IDs that are most similiar to the prompt ID at positiion 1 based on above result

In [ ]:
# @title 🥢🧾 -> 🖨️ Print Result from the 'Similiar Tokens' list from above result
list_size = 100 # @param {type:'number'}
print_ID = False # @param {type:"boolean"}
print_Similarity = True # @param {type:"boolean"}
print_Name = True # @param {type:"boolean"}
print_Divider = True # @param {type:"boolean"}

for index in range(list_size):
  id = indices[index].item()
  if (print_Name):
    print(f'{vocab[id]}') # vocab item
  if (print_ID):
    print(f'ID = {id}') # IDs
  if (print_Similarity):
    print(f'similiarity = {round(sorted[index].item()*100,2)} %') # % value
  if (print_Divider):
    print('--------')

#Print the sorted list from above result

In [ ]:

# @title 🆔 Get similarity % of two token IDs
id_for_token_A = 4567 # @param {type:'number'}
id_for_token_B = 4343 # @param {type:'number'}

similarity_str =  'The similarity between tokens A and B is ' + similarity(id_for_token_A , id_for_token_B)

print(similarity_str)

#Valid ID ranges for id_for_token_A / id_for_token_B are between 0 and 49407



# How does this notebook work?

Similiar vectors = similiar output in the SD 1.5 / SDXL / FLUX model

CLIP converts the prompt text to vectors (“tensors”) , with float32 values usually ranging from -1 to 1.

Dimensions are \[ 1x768 ] tensors for SD 1.5 , and a \[ 1x768 , 1x1024 ] tensor for SDXL and FLUX.

The SD models and FLUX converts these vectors to an image.

This notebook takes an input string , tokenizes it and matches the first token against the 49407 token vectors in the vocab.json : [https://huggingface.co/black-forest-labs/FLUX.1-dev/tree/main/tokenizer](https://www.google.com/url?q=https%3A%2F%2Fhuggingface.co%2Fblack-forest-labs%2FFLUX.1-dev%2Ftree%2Fmain%2Ftokenizer)

It finds the “most similiar tokens” in the list. Similarity is the theta angle between the token vectors.

<div>
<img src="https://huggingface.co/datasets/codeShare/sd_tokens/resolve/main/cosine.jpeg" width="300"/>
</div>

The angle is calculated using cosine similarity , where 1 = 100% similarity (parallell vectors) , and 0 = 0% similarity (perpendicular vectors).

Negative similarity is also possible.

# How can I use it?

If you are bored of prompting “girl” and want something similiar you can run this notebook and use the “chick” token at 21.88% similarity , for example

You can also run a mixed search , like “cute+girl”/2 , where for example “kpop” has a 16.71% similarity

There are some strange tokens further down the list you go. Example: tokens similiar to the token "pewdiepie</w>" (yes this is an actual token that exists in CLIP)

<div>
<img src="https://lemmy.world/pictrs/image/a1cd284e-3341-4284-9949-5f8b58d3bd1f.jpeg" width="300"/>
</div>

Each of these correspond to a unique 1x768 token vector.

The higher the ID value , the less often the token appeared in the CLIP training data.

To reiterate; this is the CLIP model training data , not the SD-model training data.

So for certain models , tokens with high ID can give very consistent results , if the SD model is trained to handle them.

Example of this can be anime models , where japanese artist names can affect the output greatly.  

Tokens with high ID will often give the "fun" output when used in very short prompts.

# What about token vector length?

If you are wondering about token magnitude,
Prompt weights like (banana:1.2) will scale the magnitude of the corresponding 1x768 tensor(s) by 1.2 . So thats how prompt token magnitude works.

Source: [https://huggingface.co/docs/diffusers/main/en/using-diffusers/weighted\_prompts](https://www.google.com/url?q=https%3A%2F%2Fhuggingface.co%2Fdocs%2Fdiffusers%2Fmain%2Fen%2Fusing-diffusers%2Fweighted_prompts)\*

So TLDR; vector direction = “what to generate” , vector magnitude = “prompt weights”

# How prompting works (technical summary)

 1. There is no correct way to prompt.

2. Stable diffusion reads your prompt left to right, one token at a time, finding association _from_ the previous token _to_ the current token _and to_ the image generated thus far (Cross Attention Rule)

3. Stable Diffusion is an optimization problem that seeks to maximize similarity to prompt and minimize similarity to negatives  (Optimization Rule)

Reference material (covers entire SD , so not good source material really, but the info is there)  : https://youtu.be/sFztPP9qPRc?si=ge2Ty7wnpPGmB0gi

# The SD pipeline

For every step (20 in total by default) for SD1.5 :

1. Prompt text =>  (tokenizer)
2. => Nx768 token vectors =>(CLIP model) =>
3. 1x768 encoding => ( the SD model / Unet ) =>
4. => _Desired_ image per Rule 3 => ( sampler)
5. => Paint a section of the image => (image)

# Disclaimer /Trivia

This notebook should be seen as a "dictionary search tool"  for the vocab.json , which is the same for SD1.5 , SDXL and FLUX. Feel free to verify this by checking the 'tokenizer' folder under each model.

vocab.json in the FLUX model , for example (1 of 2 copies) : https://huggingface.co/black-forest-labs/FLUX.1-dev/tree/main/tokenizer

I'm using Clip-vit-large-patch14 , which is used in SD 1.5 , and is one among the two tokenizers for SDXL and FLUX  : https://huggingface.co/openai/clip-vit-large-patch14/blob/main/README.md

This set of tokens has dimension 1x768.  

SDXL and FLUX uses an additional set of tokens of dimension 1x1024.

These are not included in this notebook. Feel free to include them yourselves (I would appreciate that).

To do so, you will have to download a FLUX and/or SDXL model

, and copy the 49407x1024 tensor list that is stored within the model and then save it as a .pt file.

//---//

I am aware it is actually the 1x768 text_encoding being processed into an image for the SD models + FLUX.

As such , I've included text_encoding comparison at the bottom of the Notebook.

I am also aware thar SDXL and FLUX uses additional encodings , which are not included in this notebook.

* Clip-vit-bigG for SDXL: https://huggingface.co/laion/CLIP-ViT-bigG-14-laion2B-39B-b160k/blob/main/README.md

* And the T5 text encoder for FLUX. I have 0% understanding of FLUX T5 text_encoder.

//---//

If you want them , feel free to include them yourself and share the results (cuz I probably won't)  :)!

That being said , being an encoding , I reckon the CLIP Nx768 => 1x768 should be "linear" (or whatever one might call it)

So exchange a few tokens in the Nx768 for something similiar , and the resulting 1x768 ought to be kinda similar to 1x768 we had earlier. Hopefully.

I feel its important to mention this , in case some wonder why the token-token similarity don't match the text-encoding to text-encoding similarity.

# Note regarding CLIP text encoding vs. token

*To make this disclaimer clear; Token-to-token similarity is not the same as text_encoding similarity.*

I have to say this , since it will  otherwise get (even more) confusing , as both the individual tokens , and the text_encoding have dimensions 1x768.

They are separate things. Separate results. etc.

As such , you will not get anything useful if you start comparing similarity between a token , and a text-encoding. So don't do that :)!

# What about the CLIP image encoding?

The CLIP model can also do an image_encoding of an image, where the output will be a 1x768 tensor. These _can_ be compared with the text_encoding.

Comparing CLIP image_encoding with the CLIP text_encoding for a bunch of random prompts until you find the "highest similarity" , is a method used in the CLIP interrogator : https://huggingface.co/spaces/pharmapsychotic/CLIP-Interrogator

List of random prompts for CLIP interrogator  can be found here, for reference : https://github.com/pharmapsychotic/clip-interrogator/tree/main/clip_interrogator/data

The CLIP image_encoding is not included in this Notebook.

If you spot errors / ideas for improvememts; feel free to fix the code in your own notebook and post the results.

I'd appreciate that over people saying "your math is wrong you n00b!" with no constructive feedback.

//---//

Regarding output

# What are the </w> symbols?

The whitespace symbol indicate if the tokenized item ends with whitespace ( the suffix "banana</w>" => "banana " )  or not (the prefix  "post"  in "post-apocalyptic ")

For ease of reference , I call them prefix-tokens and suffix-tokens.

Sidenote:

Prefix tokens have the unique property in that they "mutate" suffix tokens

Example:  "photo of a #prefix#-banana"

where #prefix# is a randomly selected prefix-token from the vocab.json

The hyphen "-" exists to guarantee the tokenized text splits into the written #prefix# and #suffix# token respectively.  The "-" hypen symbol can be replaced by any other special character of your choosing.

 Capital letters work too , e.g "photo of a #prefix#Abanana" since the capital letters A-Z are only listed once in the entire vocab.json.

You can also choose to omit any separator and just rawdog it with the prompt "photo of a #prefix#banana" , however know that  this may , on occasion , be tokenized as completely different tokens of lower ID:s.

Curiously , common NSFW terms found online have in the CLIP model have been purposefully fragmented into separate #prefix# and #suffix# counterparts in the vocab.json. Likely for PR-reasons.

You can verify the results using this online tokenizer: https://sd-tokenizer.rocker.boo/

<div>
<img src="https://lemmy.world/pictrs/image/43467d75-7406-4a13-93ca-cdc469f944fc.jpeg" width="300"/>
<img src="https://lemmy.world/pictrs/image/c0411565-0cb3-47b1-a788-b368924d6f17.jpeg" width="300"/>
<img src="https://lemmy.world/pictrs/image/c27c6550-a88b-4543-9bd7-067dff016be2.jpeg" width="300"/>
</div>

# What is that gibberish tokens that show up?

The gibberish tokens like "ðŁĺħ\</w>" are actually emojis!

Try writing some emojis in this online tokenizer to see the results: https://sd-tokenizer.rocker.boo/

It is a bit borked as it can't process capital letters properly.

Also note that this is not reversible.

If tokenization "😅" => ðŁĺħ</w>

Then you  can't prompt "ðŁĺħ" and expect to get the same result as the tokenized original emoji , "😅".

SD 1.5 models actually have training for Emojis.

But you have to set CLIP skip to 1 for this to work is intended.

For example, this is the result from "photo of a 🧔🏻‍♂️"


<div>
<img src="https://lemmy.world/pictrs/image/e2b51aea-6960-4ad0-867e-8ce85f2bd51e.jpeg" width="300"/>
</div>

A tutorial on stuff you can do with the vocab.list concluded.

Anyways, have fun with the notebook.

There might be some updates in the future with features not mentioned here.

//---//

https://codeandlife.com/2023/01/26/mastering-the-huggingface-clip-model-how-to-extract-embeddings-and-calculate-similarity-for-text-and-images/